# RGI17 (Southern Andes)

F. Maussion

Workaround -> use FP inventory directly

In [ ]:
import pandas as pd
import geopandas as gpd
import subprocess
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import seaborn as sns
import numpy as np
from utils import mkdir, submission_summary, needs_size_filter, size_filter, plot_map, plot_date_hist, open_zip_shapefile, find_duplicates
import os

## Files and storage paths

In [ ]:
# Region of interest
reg = 17

# go down from rgi7_scripts/workflow
data_dir = '../../rgi7_data/'

# Level 2 GLIMS files
l2_dir = os.path.join(data_dir, 'l2_sel_reg_tars')

# Output directories
output_dir = mkdir(os.path.join(data_dir, 'l3_rgi7a'))
output_dir_tar = mkdir(os.path.join(data_dir, 'l3_rgi7a_tar'))

# RGI v6 file for comparison later 
rgi6_reg_file = os.path.join(data_dir, 'l0_RGIv6', '17_rgi60_SouthernAndes.zip')

# Support data dir
support_dir = os.path.join(data_dir, 'l0_support_data')

### Load the input data

In [ ]:
# Read L2 files from GLIMS
shp = gpd.read_file('zip://' + support_dir + '/rgi17_merged.zip')

In [ ]:
shp['geom_type'] = np.array([str(type(g)) for g in shp.geometry])

In [ ]:
shp['geom_type'].value_counts()

In [ ]:
mp = shp.loc[shp['geom_type'] == "<class 'shapely.geometry.multipolygon.MultiPolygon'>"]

In [ ]:
out = []
for i, s in mp.iterrows():
    for sg in s.geometry.geoms:
        ss = s.copy()
        ss.loc['geometry'] = sg
        out.append(ss)

In [ ]:
odf = gpd.GeoDataFrame(out)

In [ ]:
xf, ax = plt.subplots(figsize=(12, 12))
odf.iloc[[1]].plot(ax=ax, edgecolor='k');

In [ ]:
odf['geom_type'] = np.array([str(type(g)) for g in odf.geometry])

In [ ]:
odf['geom_type'].value_counts()

In [ ]:
shp = pd.concat([shp, odf])

In [ ]:
shp = shp.loc[shp['geom_type'] != "<class 'shapely.geometry.multipolygon.MultiPolygon'>"]

In [ ]:
shp['geom_type'].value_counts()

In [ ]:
del shp['geom_type']

In [ ]:
shp = shp.reset_index()
del shp['index']
shp

## Outline selection geometry

In [ ]:
reg_file = os.path.join(data_dir, '00_rgi70_regions', '00_rgi70_O1Regions')
reg_f = gpd.read_file(reg_file)

In [ ]:
shp = shp.to_crs(reg_f.crs)

In [ ]:
def xy_coord(geom):
    x, y = geom.xy
    return x[0], y[0]

rp = shp.representative_point()
    
coordinates = np.array(list(rp.apply(xy_coord)))
shp['CenLon'] = coordinates[:, 0]
shp['CenLat'] = coordinates[:, 1]

rp = rp.to_frame('geometry')
rp['orig_index'] = shp.index

intersect = gpd.overlay(rp, reg_f.loc[reg_f.RGI_CODE == f'{reg:02d}'], how='intersection')

print(len(shp))
rgi7 = shp.loc[intersect['orig_index']]    
print(len(rgi7))

In [ ]:
rgi7['area'] = rgi7.to_crs({'proj':'cea'}).area

In [ ]:
# Size filter?
needs_size_filter(rgi7)

In [ ]:
print(len(rgi7))
rgi7 = size_filter(rgi7)
print(len(rgi7))

In [ ]:
rgi7['is_rgi6'] = False

### Some sanity checks 

In [ ]:
dupes = find_duplicates(rgi7)

In [ ]:
dupes.plot(edgecolor='k', facecolor='none');

In [ ]:
rgi7 = rgi7.iloc[rgi7.index != dupes.index[1]]

### Plots 

In [ ]:
rgi7['subm_id'] = 999

In [ ]:
plot_map(rgi7, reg, aspect=0.8, loc='upper left')

In [ ]:
plot_map(rgi7, reg, aspect=0.8, loc='upper left', is_rgi6=True)

In [ ]:
rgi7['src_date'] = rgi7['Date_1']

In [ ]:
plot_date_hist(rgi7, reg)

## Write out and tar 

In [ ]:
dd = mkdir(f'{output_dir}/RGI{reg:02d}/', reset=True)

print('Writing...')
rgi7.to_file(dd + f'RGI{reg:02d}.shp')

print('Taring...')
print(subprocess.run(['tar', '-zcvf', f'{output_dir_tar}/RGI{reg:02d}.tar.gz', '-C', output_dir, f'RGI{reg:02d}']))